## Import required packages

In [1]:
import requests
import pandas as pd
import FundamentalAnalysis as fa
from bs4 import BeautifulSoup


In [2]:
from __future__ import absolute_import, division, print_function, unicode_literals

#import all libraries
import numpy as np
import pandas as pd
import math
import sklearn
import sklearn.preprocessing
import datetime
import os
import matplotlib.pyplot as plt
import pandas_datareader.data as web
import seaborn as sns
import tensorflow.compat.v1 as tf
import tensorflow as tf

plt.style.use('fivethirtyeight')
%config InlineBackend.figure_format = 'retina'
%matplotlib inline

/Users/little/opt/anaconda3/lib/python3.7/site-packages/pandas_datareader/compat/__init__.py:7: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  from pandas.util.testing import assert_frame_equal


## Financial Statements

- Functions to retrieve financial data

In [3]:
def balance_sheet(stock):
    BS = requests.get(f"https://financialmodelingprep.com/api/v3/financials/balance-sheet-statement/{stock}?period=quarter")
    BS = BS.json()
    
    return(BS)
    

In [4]:
def income_statement(stock):
    income_statement = requests.get(f"https://financialmodelingprep.com/api/v3/financials/income-statement/{stock}?period=quarter")
    income_statement = income_statement.json()
    
    return(income_statement)
    

In [5]:
def cash_flow(stock):
    cash_flow = requests.get(f"https://financialmodelingprep.com/api/v3/financials/cash-flow-statement/{stock}?period=quarter")
    cash_flow = cash_flow.json()
    print(cash_flow)
    

In [6]:
def company_profile(stock):
    company_info = requests.get(f"https://financialmodelingprep.com/api/v3/company/profile/{stock}")
    company_info = company_info.json()
    
    return(company_info)

In [7]:
def financial_ratios(stock):
    company_ratio = requests.get(f"https://financialmodelingprep.com/api/v3/financial-ratios/{stock}")
    company_ratio = company_ratio.json()
    
    return(company_ratio)
    

- SP 500 Ticker

In [8]:
from bs4 import BeautifulSoup

def sp500_ticker(url):
    # function: scraping the S&P 500 companies list from Wikipedia
    
    tickers = []
    response = requests.get(url)
    
    if not response.status_code == 200:
        return None
    try:
        result_page = BeautifulSoup(response.content, 'lxml')
        table = result_page.find('table',{'class': 'wikitable sortable'})
        link = table.find_all('tr')[1:]
        for links in link:
            tickers.append(links.findAll('td')[0].text)
            
        tickers = list(map(lambda x:x.strip(), tickers))
        return tickers
    
    except:
        return None   

- Data Collection

In [9]:
def data_collection(ticker, start, end):
    
    df = web.get_data_yahoo(ticker, start, end)
    
    # Change all column headings to be lower case, and remove spacing
    df.columns = [str(x).lower().replace(' ', '_') for x in df.columns]

    return df


In [10]:
df_stock= data_collection('AAPL', datetime.date(2019,4,1), datetime.date.today())
df_stock = df_stock[['high', 'low', 'open','close']].dropna()
df_stock.tail()

high         low        open       close
Date                                                      
2020-05-08  310.350006  304.290009  305.640015  310.130005
2020-05-11  317.049988  307.239990  308.100006  315.010010
2020-05-12  319.690002  310.910004  317.829987  311.410004
2020-05-13  315.950012  303.209991  312.149994  307.649994
2020-05-14  309.790009  301.529999  304.510010  309.540009

### P/E

In [15]:
def getPE(stock):
    return float(financial_ratios(stock)['ratios'][0]['investmentValuationRatios']['priceEarningsRatio'])

In [12]:
print('P/E Ratio:')
print('MSFT: %.2f' %getPE('MSFT'))
print('AAPL: %.2f' %getPE('AAPL') )
print('AMZN: %.2f' %getPE('AMZN') )

P/E Ratio:
MSFT: 27.44
AAPL: 20.81
AMZN: 79.75


In [13]:
def getPE(stock):
    finRatios = fa.financial_ratios(stock)
    ratio = 'priceEarningsRatio'
    ROE = round(float(fa.financial_ratios(stock).loc[ratio][0]), 2)
    
    return(ROE)

- S&P 500 Companies

In [16]:
import random

url = "http://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
ticker_500 = sp500_ticker(url)

ticker_500.remove('CCL')
ticker_500.remove('CARR')
ticker_500.remove('CTVA')
ticker_500.remove('FRC')
ticker_500.remove('HSIC')
ticker_500.remove('HWM')
ticker_500.remove('J')
ticker_500.remove('K')
ticker_500.remove('LHX')
ticker_500.remove('NOW')
ticker_500.remove('RTX')
ticker_500.remove('OTIS')
ticker_500.remove('TT')
ticker_500.remove('TFC')
ticker_500.remove('VIAC')
ticker_500.remove('BRK.B')
ticker_500.remove('BF.B')

ticker_100 = ticker_500[400:500]
len(ticker_500)
#ticker_100

488

In [434]:
ticker = ticker_500

companies = fa.available_companies()
PE = pd.DataFrame({'ticker': ticker, 
                   'name': companies.loc[ticker, 'name'].values.tolist(),
                   'PE': [getPE(x) for x in ticker]})


In [417]:
stock = 'LHX'
#fa.financial_ratios(stock)
fa.financial_ratios(stock).loc[ratio][0]

'0.0'

In [435]:
PE.sort_values(by=['PE'], ascending=False).head(10)

ticker                            name       PE
398    CRM              Salesforce.com Inc  1098.69
193      F              Ford Motor Company   747.07
302    MCK            McKesson Corporation   717.88
321    MYL                      Mylan N.V.   572.80
339   NLOK             NortonLifeLock Inc.   459.80
284    LYV  Live Nation Entertainment Inc.   207.44
57    ADSK                   Autodesk Inc.   192.38
399   SBAC  SBA Communications Corporation   178.16
7      AMD     Advanced Micro Devices Inc.   157.60
242   INCY              Incyte Corporation   132.52

### ROE

Return on equity (ROE) is a measure of profitability that calculates how many dollars of profit a company generates with each dollar of shareholders' equity.

If ROE = 50% for last n quarters, company XYZ generated 0.50 of profit for every $1 of shareholders' equity last n quarters.

In [17]:
def getROE(stock):
    income_info = income_statement(stock)
    quarter_past = 4
    
    # Net Income
    net_income = float(income_info['financials'][0]['Net Income Com'])
    
    # Current total shareholders equity
    tot_equity_now = float(balance_sheet(stock)['financials'][0]['Total shareholders equity'])
    # Total shareholders equity in four quarters ago
    tot_equity_previous = float(balance_sheet(stock)['financials'][quarter_past]['Total shareholders equity'])
    # Avg Equity
    avg_equity = (tot_equity_now + tot_equity_previous)/2


    ROE = net_income/avg_equity
    
    return(ROE)
    

In [18]:
print('ROE Ratio:')
print('MSFT: %.2f%%' %(getROE('MSFT')*100))
print('AAPL: %.2f%%' %(getROE('AAPL')*100))
print('AMZN: %.2f%%' %(getROE('AMZN')*100))

ROE Ratio:
MSFT: 10.27%
AAPL: 12.21%
AMZN: 4.46%


In [38]:
def getROE(stock):
    finRatios = fa.financial_ratios(stock)
    ratio = 'returnOnEquity'
    #ROE = finRatios.loc[ratio].astype(float).round(2)[0]
    ROE = round(float(fa.financial_ratios(stock).loc[ratio][0]), 7)
    
    return(ROE)

- ROE of SP500 Company

In [19]:
import random

url = "http://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
ticker_500 = sp500_ticker(url)

ticker_500.remove('CCL')
ticker_500.remove('CARR')
ticker_500.remove('CTVA')
ticker_500.remove('FRC')
ticker_500.remove('HSIC')
ticker_500.remove('HWM')
ticker_500.remove('J')
ticker_500.remove('K')
ticker_500.remove('LHX')
ticker_500.remove('NOW')
ticker_500.remove('RTX')
ticker_500.remove('OTIS')
ticker_500.remove('TT')
ticker_500.remove('TFC')
ticker_500.remove('VIAC')
ticker_500.remove('BRK.B')
ticker_500.remove('BF.B')

ticker_100 = ticker_500[450:500]
len(ticker_500)

488

In [20]:
ticker = ticker_500

companies = fa.available_companies()
#company_name = companies.loc[ticker, :]

#past_quarter = 4
#ROE = pd.DataFrame({'ticker': ticker, 
#                    'name': company_name['name'].values.tolist(),
#                    'ROE': [getROE(*x) for x in ([[i, past_quarter] for i in ticker])]})

ROE = pd.DataFrame({'ticker': ticker, 
                    'name': companies.loc[ticker, 'name'].values.tolist(),
                    'ROE': [getROE(x) for x in ticker]})


In [31]:
ROE.sort_values(by=['ROE'], ascending=False).head(10)


ticker                            name        ROE
397   SPGI                 S&P Global Inc.  16.597403
226    HLT  Hilton Worldwide Holdings Inc.   1.573770
238   IDXX         IDEXX Laboratories Inc.   1.404544
316    MCO             Moody's Corporation   1.384005
29     AAL    American Airlines Group Inc.   1.369804
345   ORLY        O'Reilly Automotive Inc.   1.248680
276     LW       Lamb Weston Holdings Inc.   1.040149
159   EBAY                       eBay Inc.   0.932495
18    ALGN           Align Technology Inc.   0.738985
81     CPB           Campbell Soup Company   0.642041

In [33]:
ROE_new = ROE
ROE_new['Gain'] = sp500_gain

In [36]:
ROE_new.sort_values(by=['ROE'], ascending=False).head(10)

ticker                            name        ROE         Gain
397   SPGI                 S&P Global Inc.  16.597403 -5612.910110
226    HLT  Hilton Worldwide Holdings Inc.   1.573770   -99.949989
238   IDXX         IDEXX Laboratories Inc.   1.404544   -12.850021
316    MCO             Moody's Corporation   1.384005 -7720.509964
29     AAL    American Airlines Group Inc.   1.369804  -376.219990
345   ORLY        O'Reilly Automotive Inc.   1.248680   637.920013
276     LW       Lamb Weston Holdings Inc.   1.040149 -4985.730015
159   EBAY                       eBay Inc.   0.932495  -649.580008
18    ALGN           Align Technology Inc.   0.738985 -3715.399933
81     CPB           Campbell Soup Company   0.642041 -2015.890003

### P/B Ratio

P/B ratio is a financial ratio used to compare a company's current market price to its book value.

This ratio also gives some idea of whether an investor is paying too much for what would be left if the company went bankrupt immediately. A lower P/B ratio could mean the stock is undervalued. However, it could also mean something is fundamentally wrong with the company

In [37]:
def getPB(stock):
    # Current Book Value
    book_value_equity_now = float(balance_sheet(stock)['financials'][0]['Total shareholders equity'])  
    # Market Cap
    market_cap =  float(company_profile(stock)['profile']['mktCap'])

    price_to_book = market_cap / book_value_equity_now
    return (price_to_book)
     

In [38]:
print('P/B Ratio:')
print('MSFT: %.2f' %getPB('MSFT'))
print('AAPL: %.2f' %getPB('AAPL') )
print('AMZN: %.2f' %getPB('AMZN') )

P/B Ratio:
MSFT: 11.95
AAPL: 16.90
AMZN: 18.23


In [40]:
def getPB(stock):
    finRatios = fa.financial_ratios(stock)
    ratio = 'priceToBookRatio'
    PB = round(float(fa.financial_ratios(stock).loc[ratio][0]), 2)
    
    return(PB)

In [39]:
import random

url = "http://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
ticker_500 = sp500_ticker(url)

#ticker_500.remove('CARR')
#ticker_500.remove('FRC')
#ticker_500.remove('HWM')
#ticker_500.remove('RTX')
#ticker_500.remove('OTIS')
#ticker_500.remove('TT')
#ticker_500.remove('VIAC')
#ticker_500.remove('BRK.B')
#ticker_500.remove('BF.B')

ticker_500.remove('CCL')
ticker_500.remove('CARR')
ticker_500.remove('CTVA')
ticker_500.remove('FRC')
ticker_500.remove('HSIC')
ticker_500.remove('HWM')
ticker_500.remove('J')
ticker_500.remove('K')
ticker_500.remove('LHX')
ticker_500.remove('NOW')
ticker_500.remove('RTX')
ticker_500.remove('OTIS')
ticker_500.remove('TT')
ticker_500.remove('TFC')
ticker_500.remove('VIAC')
ticker_500.remove('BRK.B')
ticker_500.remove('BF.B')

ticker_100 = ticker_500[400:500]
len(ticker_500)

488

In [40]:
ticker = ticker_500

companies = fa.available_companies()
company_name = companies.loc[ticker, :]

PB = pd.DataFrame({'ticker': ticker, 
                   'name': company_name['name'].values.tolist(),
                   'PB': [getPB(x) for x in ticker]})

In [41]:
PB.sort_values(by=['PB'], ascending=False).head(10)

ticker                               name          PB
345   ORLY           O'Reilly Automotive Inc.  276.487696
238   IDXX            IDEXX Laboratories Inc.  232.801798
316    MCO                Moody's Corporation   82.667527
298     MA            Mastercard Incorporated   51.577882
281    LLY              Eli Lilly and Company   48.979943
194   FTNT                      Fortinet Inc.   43.322410
288    LOW              Lowe's Companies Inc.   42.900395
138   DXCM                        DexCom Inc.   41.070502
306    MTD  Mettler-Toledo International Inc.   39.975947
108    CLX               Clorox Company (The)   38.004889

### ROE-PB Analysis

In [46]:
ROE_PB_stock = pd.DataFrame({'ticker': ticker_500, 
                             'name': ROE['name'],
                             'ROE': ROE['ROE'],
                             'PB': PB['PB']})
ROE_PB_stock['ROE_PB_Ratio'] = ROE_PB_stock['ROE'] / ROE_PB_stock['PB']
ROE_PB_stock['Gain'] = sp500_gain

In [47]:
ROE_PB_stock.sort_values(by=['ROE_PB_Ratio'], ascending=False).head(10)

ticker                       name       ROE        PB  ROE_PB_Ratio  \
45     APA         Apache Corporation -1.560160 -3.183585      0.490064   
339   NLOK        NortonLifeLock Inc.  0.390180  1.401862      0.278330   
480    XRX          Xerox Corporation  0.154456  0.565019      0.273365   
18    ALGN      Align Technology Inc.  0.738985  5.601774      0.131920   
307    MGM  MGM Resorts International  0.107869  0.837828      0.128749   
49    APTV                  Aptiv PLC  0.374776  3.255809      0.115110   
270    KSS         Kohl's Corporation  0.048283  0.487957      0.098949   
81     CPB      Campbell Soup Company  0.642041  6.507965      0.098655   
305    MET               MetLife Inc.  0.036402  0.418828      0.086914   
335    JWN             Nordstrom Inc.  0.207343  2.657403      0.078025   

            Gain  
45  -1402.349997  
339 -1041.639997  
480 -3233.539974  
18  -3715.399933  
307  -153.569994  
49  -2045.159985  
270 -6058.079983  
81  -2015.890003  
305   -42.699986  
335  -148.330004

In [48]:
ROE_min = 0.1
PB_min = 1.0
PB_max = 50

ROE_PB_new = ROE_PB_stock.loc[(ROE_PB_stock['ROE'] > ROE_min) & 
                              ((ROE_PB_stock['PB'] < PB_max) & (ROE_PB_stock['PB'] > PB_min))]
ROE_PB_new.sort_values(by=['ROE_PB_Ratio'], ascending=False).head(10)

ticker                                name       ROE         PB  \
339   NLOK                 NortonLifeLock Inc.  0.390180   1.401862   
18    ALGN               Align Technology Inc.  0.738985   5.601774   
49    APTV                           Aptiv PLC  0.374776   3.255809   
81     CPB               Campbell Soup Company  0.642041   6.507965   
335    JWN                      Nordstrom Inc.  0.207343   2.657403   
159   EBAY                           eBay Inc.  0.932495  13.972325   
383     RL            Ralph Lauren Corporation  0.103270   1.556496   
236    HII  Huntington Ingalls Industries Inc.  0.195232   4.388837   
67     BBY                   Best Buy Co. Inc.  0.219602   5.842113   
276     LW           Lamb Weston Holdings Inc.  1.040149  28.378770   

     ROE_PB_Ratio         Gain  
339      0.278330 -1041.639997  
18       0.131920 -3715.399933  
49       0.115110 -2045.159985  
81       0.098655 -2015.890003  
335      0.078025  -148.330004  
159      0.066739  -649.580008  
383      0.066348 -1700.299988  
236      0.044484 -9434.359985  
67       0.037589   -77.450001  
276      0.036652 -4985.730015

In [49]:
ROE_PB_new.sort_values(by=['ROE_PB_Ratio'], ascending=False).tail(10)

ticker                       name       ROE         PB  ROE_PB_Ratio  \
108    CLX       Clorox Company (The)  0.326558  38.004889      0.008593   
487    ZTS        Zoetis Inc. Class A  0.163826  21.854532      0.007496   
47    AAPL                 Apple Inc.  0.122083  16.899051      0.007224   
355   PAYC       Paycom Software Inc.  0.126239  25.706911      0.004911   
381   QCOM      QUALCOMM Incorporated  0.135436  27.925603      0.004850   
293   MKTX  MarketAxess Holdings Inc.  0.104709  23.568113      0.004443   
325   NFLX               Netflix Inc.  0.100489  23.316276      0.004310   
288    LOW      Lowe's Companies Inc.  0.181624  42.900395      0.004234   
392    ROK   Rockwell Automation Inc.  0.135098  37.153979      0.003636   
194   FTNT              Fortinet Inc.  0.130457  43.322410      0.003011   

            Gain  
108  -916.069992  
487 -4800.649971  
47     53.209991  
355 -5892.140053  
381 -2916.139999  
293   245.329865  
325 -9530.899933  
288 -5263.580055  
392 -6319.619919  
194  -258.119995

In [174]:
ROE_PB_new.sort_values(by=['ROE_PB_Ratio'], ascending=False).tail(10)

ticker                               name       ROE         PB  \
356   ORCL                 Oracle Corporation  0.135498  11.760295   
173     EL  Estee Lauder Companies Inc. (The)  0.133169  12.506120   
114     KO            Coca-Cola Company (The)  0.113564  10.740852   
387   QCOM              QUALCOMM Incorporated  0.173377  17.693951   
316   MSFT              Microsoft Corporation  0.115201  11.873034   
111    CLX               Clorox Company (The)  0.285274  44.069008   
300    MAR             Marriott International  0.190574  37.232378   
294    LOW              Lowe's Companies Inc.  0.181624  36.108919   
34     AMT  American Tower Corporation (REIT)  0.108300  21.751552   
287    LLY              Eli Lilly and Company  0.152366  42.802869   

     ROE_PB_Ratio  
356      0.011522  
173      0.010648  
114      0.010573  
387      0.009799  
316      0.009703  
111      0.006473  
300      0.005118  
294      0.005030  
34       0.004979  
287      0.003560

In [186]:
print('ROE/PB Ratio:')
print('MSFT: %.4f' %(getROE('MSFT', 20)/getPB('MSFT')))
print('AAPL: %.4f' %(getROE('AAPL', 20)/getPB('AAPL')))
print('AMZN: %.4f' %(getROE('AMZN', 20)/getPB('AMZN')))

ROE/PB Ratio:
MSFT: 0.0097
AAPL: 0.0150
AMZN: 0.0049


In [227]:
stock_test = 'AMZN'
print('%s ROE: %.4f' %(stock_test, getROE(stock_test, 20)))
print('%s PB: %.4f' %(stock_test, getPB(stock_test)))
print('%s ROE-PB: %.4f' %(stock_test, getROE(stock_test, 20)/getPB(stock_test)))

AMZN ROE: 0.0898
AMZN PB: 19.3171
AMZN ROE-PB: 0.0046


### ROE - PB - PE

In [564]:
ratios = pd.DataFrame({'ticker': ticker_500, 
                       'name': ROE['name'],
                       'ROE': ROE['ROE'],
                       'PB': PB['PB'],
                      'PE': PE['PE']})
#ratios['ROE_PB_Ratio'] = ratios['ROE'] / ratios['PB']
ratios.head(10)

ticker                             name       ROE     PB      PE
0    MMM                       3M Company  0.546039  12.41   22.73
1    ABT              Abbott Laboratories  0.118599   4.81   40.52
2   ABBV                      AbbVie Inc. -0.964513 -14.82   15.37
3   ABMD                     ABIOMED Inc.  0.276464  16.68   60.35
4    ACN  Accenture plc Class A (Ireland)  0.331675   8.52   25.68
5   ATVI          Activision Blizzard Inc  0.117376   3.25   27.67
6   ADBE       Adobe Systems Incorporated  0.280286  15.28   54.50
7    AMD      Advanced Micro Devices Inc.  0.120623  19.01  157.60
8    AAP       Advance Auto Parts Inc W/I  0.119366   3.69   30.91
9    AES              The AES Corporation  0.101135   4.19   41.46

In [493]:
ratios.sort_values(by=['PE'], ascending=False).head()

ticker                  name       ROE    PB       PE
398    CRM    Salesforce.com Inc  0.003719  4.09  1098.69
193      F    Ford Motor Company  0.001416  1.06   747.07
302    MCK  McKesson Corporation  0.004201  3.02   717.88
321    MYL            Mylan N.V.  0.001414  0.81   572.80
339   NLOK   NortonLifeLock Inc.  0.005400  7.85   459.80

In [53]:
stock_test = 'DIS'
print('%s PE: %.4f' %(stock_test, getPE(stock_test)))
print('%s ROE: %.2f%%' %(stock_test, getROE(stock_test)*100))
print('%s PB: %.4f' %(stock_test, getPB(stock_test)))
print('%s ROE-PB: %.4f' %(stock_test, getROE(stock_test)/getPB(stock_test)))

DIS PE: 20.6498
DIS ROE: 12.44%
DIS PB: 2.5700
DIS ROE-PB: 0.0484


## DCF

In [2]:
ticker = 'AMZN'
DCFquarterly = fa.discounted_cash_flow(ticker, period="quarterly")
DCFquarterly

2020        2019        2018        2017        2016  \
date         2020-04-24  2019-12-31  2018-12-31  2017-12-31  2016-12-31   
Stock Price     2399.45     1870.68     1670.43     1437.82      830.38   
DCF             2471.06     1943.74     1735.63     1480.57     871.169   

                   2015        2014        2013        2012        2011  \
date         2015-12-31  2014-12-31  2013-12-31  2012-12-31  2011-12-31   
Stock Price         587      354.53      403.01      272.76      192.15   
DCF             621.026     386.039     421.955     290.605     203.781   

                   2010        2009  
date         2010-12-31  2009-12-31  
Stock Price      171.14      125.41  
DCF              179.59     140.113

In [29]:
ticker = 'AMZN'
DCFquarterly = fa.discounted_cash_flow(ticker, period="quarterly")

dcf_quarterly1=pd.DataFrame({
    'date':DCFquarterly.iloc[0],
    'stock price': DCFquarterly.iloc[1],
    'DCF': DCFquarterly.iloc[2]
})
new_dcf_quarterly=dcf_quarterly1.sort_values(by='date')
new_dcf_quarterly.tail(6)

date stock price      DCF
2015  2015-12-31         587  621.026
2016  2016-12-31      830.38  871.169
2017  2017-12-31     1437.82  1480.57
2018  2018-12-31     1670.43  1735.63
2019  2019-12-31     1870.68  1943.74
2020  2020-04-27        2376  2447.61

In [20]:
(new_dcf_quarterly.tail(1)['DCF'] -  new_dcf_quarterly.tail(1)['stock price']) /new_dcf_quarterly.tail(1)['stock price']


2020    0.0483818
dtype: object

In [9]:
new_dcf_quarterly.loc[new_dcf_quarterly.index.values[len(new_dcf_quarterly)-1]]

date           2020-04-24
stock price       2399.45
DCF               2471.06
Name: 2020, dtype: object

## LSTM

In [21]:
from collections import deque
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
#import tensorflow as tf
import random
        
class Agent:

    LEARNING_RATE = 0.01
    BATCH_SIZE = 100
    LAYER_SIZE = 3
    OUTPUT_SIZE = 3
    EPSILON = 0.5
    DECAY_RATE = 0.5
    MIN_EPSILON = 0.1
    GAMMA = 0.1
    MEMORIES = deque()
    MEMORY_SIZE = 300
    
#    import tensorflow.compat.v1 as tf
#tf.disable_v2_behavior()
    
    def __init__(self, state_size, window_size, trend, skip):
        self.state_size = state_size
        self.window_size = window_size
        self.half_window = window_size // 2
        self.trend = trend
        self.skip = skip
        #tf.compat.v1.reset_default_graph()
        tf.reset_default_graph()
        
        self.INITIAL_FEATURES = np.zeros((4, self.state_size))
        
        #self.X = tf.compat.v1.placeholder(tf.float32, (None, None, self.state_size))
        #self.Y = tf.compat.v1.placeholder(tf.float32, (None, self.OUTPUT_SIZE))
        
        self.X = tf.placeholder(tf.float32, (None, None, self.state_size))
        self.Y = tf.placeholder(tf.float32, (None, self.OUTPUT_SIZE))
        
        cell = tf.nn.rnn_cell.LSTMCell(self.LAYER_SIZE, state_is_tuple = False)
        self.hidden_layer = tf.placeholder(tf.float32, (None, 2 * self.LAYER_SIZE))
        self.rnn,self.last_state = tf.nn.dynamic_rnn(inputs=self.X,cell=cell,
                                                    dtype=tf.float32,
                                                    initial_state=self.hidden_layer)
        self.logits = tf.layers.dense(self.rnn[:,-1], self.OUTPUT_SIZE)
        self.cost = tf.reduce_sum(tf.square(self.Y - self.logits))
        self.optimizer = tf.train.AdamOptimizer(learning_rate = self.LEARNING_RATE).minimize(self.cost)
        self.sess = tf.InteractiveSession()
        self.sess.run(tf.global_variables_initializer())
    
    def _memorize(self, state, action, reward, new_state, dead, rnn_state):
        self.MEMORIES.append((state, action, reward, new_state, dead, rnn_state))
        if len(self.MEMORIES) > self.MEMORY_SIZE:
            self.MEMORIES.popleft()

    def _construct_memories(self, replay):
        states = np.array([a[0] for a in replay])
        new_states = np.array([a[3] for a in replay])
        init_values = np.array([a[-1] for a in replay])
        Q = self.sess.run(self.logits, feed_dict={self.X:states, self.hidden_layer:init_values})
        Q_new = self.sess.run(self.logits, feed_dict={self.X:new_states, self.hidden_layer:init_values})
        replay_size = len(replay)
        X = np.empty((replay_size, 4, self.state_size))
        Y = np.empty((replay_size, self.OUTPUT_SIZE))
        INIT_VAL = np.empty((replay_size, 2 * self.LAYER_SIZE))
        for i in range(replay_size):
            state_r, action_r, reward_r, new_state_r, dead_r, rnn_memory = replay[i]
            target = Q[i]
            target[action_r] = reward_r
            if not dead_r:
                target[action_r] += self.GAMMA * np.amax(Q_new[i])
            X[i] = state_r
            Y[i] = target
            INIT_VAL[i] = rnn_memory
        return X, Y, INIT_VAL
    
    def get_state(self, t):
        window_size = self.window_size + 1
        d = t - window_size + 1
        block = self.trend[d : t + 1] if d >= 0 else -d * [self.trend[0]] + self.trend[0 : t + 1]
        res = []
        for i in range(window_size - 1):
            res.append(block[i + 1] - block[i])
        return np.array(res)
    
    def buy(self, initial_money):
        starting_money = initial_money
        states_sell = []
        states_buy = []
        inventory = []
        state = self.get_state(0)
        init_value = np.zeros((1, 2 * self.LAYER_SIZE))
        for k in range(self.INITIAL_FEATURES.shape[0]):
            self.INITIAL_FEATURES[k,:] = state
        for t in range(0, len(self.trend) - 1, self.skip):
            action, last_state = self.sess.run([self.logits,self.last_state],
                                                feed_dict={self.X:[self.INITIAL_FEATURES],
                                                            self.hidden_layer:init_value})
            action, init_value = np.argmax(action[0]), last_state
            next_state = self.get_state(t + 1)
            
            if action == 1 and initial_money >= self.trend[t]:
                inventory.append(self.trend[t])
                initial_money -= self.trend[t]
                states_buy.append(t)
                print('day %d: buy 1 unit at price %f, total balance %f'% (t, self.trend[t], initial_money))
            
            elif action == 2 and len(inventory):
                bought_price = inventory.pop(0)
                initial_money += self.trend[t]
                states_sell.append(t)
                try:
                    invest = ((close[t] - bought_price) / bought_price) * 100
                except:
                    invest = 0
                print(
                    'day %d, sell 1 unit at price %f, investment %f %%, total balance %f,'
                    % (t, close[t], invest, initial_money)
                )
            
            new_state = np.append([self.get_state(t + 1)], self.INITIAL_FEATURES[:3, :], axis = 0)
            self.INITIAL_FEATURES = new_state
        invest = ((initial_money - starting_money) / starting_money) * 100
        total_gains = initial_money - starting_money
        return states_buy, states_sell, total_gains, invest
            
    
    def train(self, iterations, checkpoint, initial_money):
        for i in range(iterations):
            total_profit = 0
            inventory = []
            state = self.get_state(0)
            starting_money = initial_money
            init_value = np.zeros((1, 2 * self.LAYER_SIZE))
            for k in range(self.INITIAL_FEATURES.shape[0]):
                self.INITIAL_FEATURES[k,:] = state
            for t in range(0, len(self.trend) - 1, self.skip):
                
                if np.random.rand() < self.EPSILON:
                    action = np.random.randint(self.OUTPUT_SIZE)
                else:
                    action, last_state = self.sess.run([self.logits,
                                                  self.last_state],
                                                  feed_dict={self.X:[self.INITIAL_FEATURES],
                                                             self.hidden_layer:init_value})
                    action, init_value = np.argmax(action[0]), last_state
                    
                next_state = self.get_state(t + 1)
                
                if action == 1 and starting_money >= self.trend[t]:
                    inventory.append(self.trend[t])
                    starting_money -= self.trend[t]
                
                elif action == 2 and len(inventory) > 0:
                    bought_price = inventory.pop(0)
                    total_profit += self.trend[t] - bought_price
                    starting_money += self.trend[t]
                    
                invest = ((starting_money - initial_money) / initial_money)
                new_state = np.append([self.get_state(t + 1)], self.INITIAL_FEATURES[:3, :], axis = 0)
                self._memorize(self.INITIAL_FEATURES, action, invest, new_state, 
                               starting_money < initial_money, init_value[0])
                self.INITIAL_FEATURES = new_state
                batch_size = min(len(self.MEMORIES), self.BATCH_SIZE)
                replay = random.sample(self.MEMORIES, batch_size)
                X, Y, INIT_VAL = self._construct_memories(replay)
                
                cost, _ = self.sess.run([self.cost, self.optimizer], 
                                        feed_dict={self.X: X, self.Y:Y,
                                                  self.hidden_layer: INIT_VAL})
                self.EPSILON = self.MIN_EPSILON + (1.0 - self.MIN_EPSILON) * np.exp(-self.DECAY_RATE * i)
                
            if (i+1) % checkpoint == 0:
                print('epoch: %d, total rewards: %f.3, cost: %f, total money: %f'%(i + 1, total_profit, cost,
                                                                                  starting_money))

Instructions for updating:
non-resource variables are not supported in the long term


### Evaluation

In [18]:
df_stock= data_collection('AAPL', datetime.date(2020,3,1), datetime.date(2020,4,1))
df_stock = df_stock[['high', 'low', 'open','close']].dropna()
df_stock.head()

high         low        open       close
Date                                                      
2020-03-02  301.440002  277.720001  282.279999  298.809998
2020-03-03  304.000000  285.799988  303.670013  289.320007
2020-03-04  303.399994  293.130005  296.440002  302.739990
2020-03-05  299.549988  291.410004  295.519989  292.920013
2020-03-06  290.820007  281.230011  282.000000  289.029999

In [22]:
close = df_stock.close.values.tolist()
initial_money = 10000
window_size = 60
skip = 1
batch_size = 300
agent = Agent(state_size = window_size, 
              window_size = window_size, 
              trend = close, 
              skip = skip)
#agent.train(iterations = 25, checkpoint = 5, initial_money = initial_money)

states_buy, states_sell, total_gains, invest = agent.buy(initial_money = initial_money)


Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use keras.layers.Dense instead.
Instructions for updating:
Please use `layer.__call__` method instead.
day 18: buy 1 unit at price 204.300003, total balance 9795.699997
day 27, sell 1 unit at price 200.720001, investment -1.752326 %, total balance 9996.419998,
day 30: buy 1 unit at price 188.660004, total balance 9807.759995
day 32, sell 1 unit at price 190.080002, investment 0.752676 %, total balance 9997.839996,
day 34: buy 1 unit at price 183.089996, total balance 9814.750000
day 36: buy 1 unit at price 182.779999, total balance 9631.970001
day 38,

In [20]:
total_gains

-733.97998046875

In [23]:
def stock_gain(stock):
    #df_stock= data_collection(stock, datetime.date(2019,4,1), datetime.date.today())
    df_stock= data_collection(stock, datetime.date(2019,1,1), datetime.date(2019,12,31))
    df_stock = df_stock[['high', 'low', 'open','close']].dropna()
    
    close = df_stock.close.values.tolist()
    initial_money = 10000
    window_size = 60
    skip = 1
    batch_size = 300
    agent = Agent(state_size = window_size, 
                  window_size = window_size, 
                  trend = close, 
                  skip = skip)
    
    states_buy, states_sell, total_gains, invest = agent.buy(initial_money = initial_money)
    
    return total_gains

In [28]:
stock_list = ticker_500
stock_list

['MMM',
 'ABT',
 'ABBV',
 'ABMD',
 'ACN',
 'ATVI',
 'ADBE',
 'AMD',
 'AAP',
 'AES',
 'AFL',
 'A',
 'APD',
 'AKAM',
 'ALK',
 'ALB',
 'ARE',
 'ALXN',
 'ALGN',
 'ALLE',
 'ADS',
 'LNT',
 'ALL',
 'GOOGL',
 'GOOG',
 'MO',
 'AMZN',
 'AMCR',
 'AEE',
 'AAL',
 'AEP',
 'AXP',
 'AIG',
 'AMT',
 'AWK',
 'AMP',
 'ABC',
 'AME',
 'AMGN',
 'APH',
 'ADI',
 'ANSS',
 'ANTM',
 'AON',
 'AOS',
 'APA',
 'AIV',
 'AAPL',
 'AMAT',
 'APTV',
 'ADM',
 'ANET',
 'AJG',
 'AIZ',
 'T',
 'ATO',
 'ADSK',
 'ADP',
 'AZO',
 'AVB',
 'AVY',
 'BKR',
 'BLL',
 'BAC',
 'BK',
 'BAX',
 'BDX',
 'BBY',
 'BIIB',
 'BLK',
 'BA',
 'BKNG',
 'BWA',
 'BXP',
 'BSX',
 'BMY',
 'AVGO',
 'BR',
 'CHRW',
 'COG',
 'CDNS',
 'CPB',
 'COF',
 'CAH',
 'KMX',
 'CAT',
 'CBOE',
 'CBRE',
 'CDW',
 'CE',
 'CNC',
 'CNP',
 'CTL',
 'CERN',
 'CF',
 'SCHW',
 'CHTR',
 'CVX',
 'CMG',
 'CB',
 'CHD',
 'CI',
 'CINF',
 'CTAS',
 'CSCO',
 'C',
 'CFG',
 'CTXS',
 'CLX',
 'CME',
 'CMS',
 'KO',
 'CTSH',
 'CL',
 'CMCSA',
 'CMA',
 'CAG',
 'CXO',
 'COP',
 'ED',
 'STZ',
 'COO',
 'C

In [29]:
sp500_gain = [stock_gain(x) for x in stock_list]

/Users/little/opt/anaconda3/lib/python3.7/site-packages/tensorflow_core/python/client/session.py:1752: UserWarning: An interactive session is already active. This can cause out-of-memory errors in some cases. You must explicitly call `InteractiveSession.close()` to release resources held by the other session(s).
  warnings.warn('An interactive session is already active. This can '


day 13: buy 1 unit at price 192.259995, total balance 9807.740005
day 15: buy 1 unit at price 192.520004, total balance 9615.220001
day 16: buy 1 unit at price 195.899994, total balance 9419.320007
day 17, sell 1 unit at price 205.279999, investment 6.772082 %, total balance 9612.520004,
day 18, sell 1 unit at price 204.300003, investment 6.118844 %, total balance 9809.470001,
day 20: buy 1 unit at price 200.300003, total balance 9609.169998
day 22, sell 1 unit at price 209.149994, investment 6.763655 %, total balance 9809.380005,
day 23, sell 1 unit at price 211.750000, investment 5.716424 %, total balance 10010.500000,
day 29: buy 1 unit at price 209.720001, total balance 9800.779999
day 31: buy 1 unit at price 208.860001, total balance 9591.919998
day 32: buy 1 unit at price 208.410004, total balance 9383.509995
day 33: buy 1 unit at price 208.529999, total balance 9174.979996
day 34, sell 1 unit at price 183.089996, investment -12.697885 %, total balance 9382.750000,
day 36, sell 1

day 238: buy 1 unit at price 168.740005, total balance 9652.689987
day 239, sell 1 unit at price 248.229996, investment 47.107969 %, total balance 9821.249985,
day 241: buy 1 unit at price 170.750000, total balance 9650.499985
day 244, sell 1 unit at price 244.779999, investment 43.355783 %, total balance 9822.649979,
day 246: buy 1 unit at price 178.470001, total balance 9644.179977
day 248, sell 1 unit at price 245.520004, investment 37.569341 %, total balance 9820.769974,
day 3: buy 1 unit at price 69.129997, total balance 9930.870003
day 4: buy 1 unit at price 68.300003, total balance 9862.570000
day 5: buy 1 unit at price 69.440002, total balance 9793.129997
day 12, sell 1 unit at price 203.130005, investment 193.837716 %, total balance 9864.549995,
day 13, sell 1 unit at price 203.860001, investment 198.477294 %, total balance 9936.039993,
day 14, sell 1 unit at price 204.529999, investment 194.542039 %, total balance 10005.949997,
day 16: buy 1 unit at price 71.150002, total bal

day 1: buy 1 unit at price 302.290009, total balance 9697.709991
day 2: buy 1 unit at price 313.440002, total balance 9384.269989
day 3: buy 1 unit at price 314.799988, total balance 9069.470001
day 4: buy 1 unit at price 318.420013, total balance 8751.049988
day 5: buy 1 unit at price 336.399994, total balance 8414.649994
day 6: buy 1 unit at price 335.130005, total balance 8079.519989
day 7: buy 1 unit at price 323.799988, total balance 7755.720001
day 9: buy 1 unit at price 325.609985, total balance 7430.110016
day 10: buy 1 unit at price 324.130005, total balance 7105.980011
day 11: buy 1 unit at price 330.320007, total balance 6775.660004
day 12: buy 1 unit at price 333.739990, total balance 6441.920013
day 13, sell 1 unit at price 203.860001, investment -32.561449 %, total balance 6778.050018,
day 14: buy 1 unit at price 336.980011, total balance 6441.070007
day 15: buy 1 unit at price 348.500000, total balance 6092.570007
day 16: buy 1 unit at price 349.369995, total balance 574

day 172: buy 1 unit at price 186.809998, total balance 2297.509872
day 173: buy 1 unit at price 191.820007, total balance 2105.689865
day 174: buy 1 unit at price 191.070007, total balance 1914.619858
day 175: buy 1 unit at price 188.020004, total balance 1726.599854
day 176: buy 1 unit at price 186.410004, total balance 1540.189850
day 177: buy 1 unit at price 190.539993, total balance 1349.649857
day 178, sell 1 unit at price 271.459991, investment 2.018112 %, total balance 1540.189850,
day 179: buy 1 unit at price 190.669998, total balance 1349.519852
day 180, sell 1 unit at price 279.859985, investment 6.536215 %, total balance 1541.839859,
day 181, sell 1 unit at price 280.410004, investment 7.609954 %, total balance 1734.599854,
day 182: buy 1 unit at price 186.009995, total balance 1548.589859
day 183, sell 1 unit at price 280.019989, investment 10.352705 %, total balance 1732.939865,
day 184, sell 1 unit at price 279.440002, investment 7.282989 %, total balance 1918.219864,
day

...

day 2: buy 1 unit at price 91.459999, total balance 9908.540001
day 3: buy 1 unit at price 91.360001, total balance 9817.180000
day 4, sell 1 unit at price 197.000000, investment 115.394710 %, total balance 9908.360001,
day 6, sell 1 unit at price 199.500000, investment 118.366899 %, total balance 10000.150002,
day 12: buy 1 unit at price 92.360001, total balance 9907.790001
day 13, sell 1 unit at price 203.860001, investment 120.723256 %, total balance 9999.840004,
day 19: buy 1 unit at price 93.449997, total balance 9906.390007
day 20: buy 1 unit at price 93.980003, total balance 9812.410004
day 27: buy 1 unit at price 93.260002, total balance 9719.150002
day 30: buy 1 unit at price 93.849998, total balance 9625.300003
day 31: buy 1 unit at price 94.120003, total balance 9531.180000
day 32: buy 1 unit at price 94.519997, total balance 9436.660004
day 33, sell 1 unit at price 189.000000, investment 102.247198 %, total balance 9531.380005,
day 34, sell 1 unit at price 183.089996, inves

day 244: buy 1 unit at price 253.130005, total balance 9692.430023
day 245, sell 1 unit at price 229.240005, investment -10.739039 %, total balance 9944.920029,
day 246, sell 1 unit at price 224.369995, investment -13.129164 %, total balance 10201.650040,
day 248, sell 1 unit at price 245.520004, investment -3.006361 %, total balance 10456.070038,
day 1: buy 1 unit at price 100.430000, total balance 9899.570000
day 2, sell 1 unit at price 195.350006, investment 94.513597 %, total balance 10003.430000,
day 4: buy 1 unit at price 101.570000, total balance 9901.860001
day 13: buy 1 unit at price 103.919998, total balance 9797.940002
day 16, sell 1 unit at price 207.160004, investment 103.957866 %, total balance 9905.350006,
day 17, sell 1 unit at price 205.279999, investment 97.536569 %, total balance 10011.190002,
day 18: buy 1 unit at price 105.660004, total balance 9905.529999
day 26: buy 1 unit at price 120.580002, total balance 9784.949997
day 31: buy 1 unit at price 123.650002, tota

day 249, sell 1 unit at price 258.440002, investment 88.628577 %, total balance 6470.739944,
day 250, sell 1 unit at price 247.740005, investment 78.796196 %, total balance 6619.489944,
day 1: buy 1 unit at price 41.349998, total balance 9958.650002
day 8, sell 1 unit at price 198.949997, investment 381.136649 %, total balance 10002.970001,
day 11: buy 1 unit at price 46.590000, total balance 9956.380001
day 12: buy 1 unit at price 47.049999, total balance 9909.330002
day 13: buy 1 unit at price 46.529999, total balance 9862.800003
day 14, sell 1 unit at price 204.529999, investment 338.999781 %, total balance 9910.910004,
day 15, sell 1 unit at price 207.479996, investment 340.977681 %, total balance 9959.510002,
day 16, sell 1 unit at price 207.160004, investment 345.218158 %, total balance 10008.190002,
day 23: buy 1 unit at price 48.830002, total balance 9959.360001
day 24: buy 1 unit at price 48.980000, total balance 9910.380001
day 25: buy 1 unit at price 49.299999, total balance

day 2: buy 1 unit at price 84.760002, total balance 9915.239998
day 3: buy 1 unit at price 85.269997, total balance 9829.970001
day 4: buy 1 unit at price 86.540001, total balance 9743.430000
day 5: buy 1 unit at price 86.230003, total balance 9657.199997
day 6, sell 1 unit at price 199.500000, investment 135.370452 %, total balance 9743.099998,
day 7, sell 1 unit at price 200.619995, investment 135.276185 %, total balance 9829.159996,
day 8, sell 1 unit at price 198.949997, investment 129.893685 %, total balance 9913.659996,
day 10: buy 1 unit at price 83.209999, total balance 9830.449997
day 11, sell 1 unit at price 199.250000, investment 131.068065 %, total balance 9914.699997,
day 12, sell 1 unit at price 203.130005, investment 144.117302 %, total balance 9999.289993,
day 17: buy 1 unit at price 83.650002, total balance 9915.639992
day 20, sell 1 unit at price 200.669998, investment 139.892402 %, total balance 10001.799995,
day 21: buy 1 unit at price 87.139999, total balance 9914.

day 219: buy 1 unit at price 116.449997, total balance 6129.630020
day 220: buy 1 unit at price 116.250000, total balance 6013.380020
day 221: buy 1 unit at price 117.919998, total balance 5895.460022
day 222: buy 1 unit at price 118.800003, total balance 5776.660019
day 223: buy 1 unit at price 120.330002, total balance 5656.330017
day 224: buy 1 unit at price 119.559998, total balance 5536.770020
day 225: buy 1 unit at price 120.220001, total balance 5416.550018
day 227, sell 1 unit at price 288.079987, investment 128.272578 %, total balance 5537.160019,
day 228, sell 1 unit at price 292.649994, investment 133.671350 %, total balance 5659.050018,
day 229: buy 1 unit at price 121.629997, total balance 5537.420021
day 230: buy 1 unit at price 120.519997, total balance 5416.900024
day 231: buy 1 unit at price 119.910004, total balance 5296.990021
day 232: buy 1 unit at price 120.529999, total balance 5176.460022
day 233: buy 1 unit at price 119.739998, total balance 5056.720024
day 235:

In [30]:
sp500_gain

[-179.2300262451172,
 -168.82000732421875,
 -8315.099983215332,
 -9500.6201171875,
 16.3900146484375,
 -16.780017852783203,
 -294.05995178222656,
 -211.76999473571777,
 -394.3799285888672,
 -1751.6300134658813,
 -5.71002197265625,
 -2238.8400115966797,
 -2487.4100494384766,
 -2840.53999710083,
 -2635.2000122070312,
 -619.7499809265137,
 -952.0000305175781,
 -101.1199722290039,
 -3715.399932861328,
 -9926.479988098145,
 -3350.6000442504883,
 22.930004119873047,
 -6715.4899826049805,
 -3191.7900390625,
 -5682.5601806640625,
 8.989994049072266,
 -35.3602294921875,
 -456.0000009536743,
 -684.6400299072266,
 -376.2199897766113,
 -18.730018615722656,
 -9806.63003540039,
 -1996.6699752807617,
 -8982.690017700195,
 -308.4400177001953,
 -715.9500045776367,
 -45.450042724609375,
 -1840.0600204467773,
 -1243.0500030517578,
 27.839988708496094,
 -7371.629997253418,
 -3982.959915161133,
 -1744.8502197265625,
 -2772.5900115966797,
 -156.62998962402344,
 -1402.3499965667725,
 -157.20001602172852,
 53

###  Comparison

In [565]:
ratios['gain'] = sp500_gain
ratios

ticker                             name       ROE     PB     PE  \
0      MMM                       3M Company  0.546039  12.41  22.73   
1      ABT              Abbott Laboratories  0.118599   4.81  40.52   
2     ABBV                      AbbVie Inc. -0.964513 -14.82  15.37   
3     ABMD                     ABIOMED Inc.  0.276464  16.68  60.35   
4      ACN  Accenture plc Class A (Ireland)  0.331675   8.52  25.68   
..     ...                              ...       ...    ...    ...   
483    YUM                 Yum! Brands Inc. -0.161427  -3.84  23.78   
484   ZBRA   Zebra Technologies Corporation  0.315356   7.28  23.09   
485    ZBH      Zimmer Biomet Holdings Inc. -0.033643   2.10 -62.49   
486   ZION             Zions Bancorporation  0.112167   1.24  11.02   
487    ZTS              Zoetis Inc. Class A  0.653547  20.69  31.65   

            gain  
0   -6914.350052  
1      24.759995  
2   -1696.129951  
3   -9803.390045  
4   -8183.230087  
..           ...  
483  -581.099991  
484  -604.639954  
485 -7024.089989  
486 -4387.509991  
487  -696.459991  

[488 rows x 6 columns]

In [551]:
ROE_min = 0.1
PB_min = 1.0
PB_max = 50

ratios_new = ratios.loc[(ratios['ROE'] > ROE_min) & 
                              ((ratios['PB'] < PB_max) & (ratios['PB'] > PB_min))]
ratios_new
#ratios_new.sort_values(by=['ROE_PB_Ratio'], ascending=False).head(10)

ticker                             name       ROE     PB     PE  \
0      MMM                       3M Company  0.546039  12.41  22.73   
1      ABT              Abbott Laboratories  0.118599   4.81  40.52   
3     ABMD                     ABIOMED Inc.  0.276464  16.68  60.35   
4      ACN  Accenture plc Class A (Ireland)  0.331675   8.52  25.68   
5     ATVI          Activision Blizzard Inc  0.117376   3.25  27.67   
..     ...                              ...       ...    ...    ...   
481   XLNX                      Xilinx Inc.  0.310937  11.07  35.60   
482    XYL                   Xylem Inc. New  0.135610   4.66  34.36   
484   ZBRA   Zebra Technologies Corporation  0.315356   7.28  23.09   
486   ZION             Zions Bancorporation  0.112167   1.24  11.02   
487    ZTS              Zoetis Inc. Class A  0.653547  20.69  31.65   

     ROE_PB_Ratio         gain  
0        0.044000 -6914.350052  
1        0.024657    24.759995  
3        0.016575 -9803.390045  
4        0.038929 -8183.230087  
5        0.036116  -143.549988  
..            ...          ...  
481      0.028088 -9297.179962  
482      0.029101 -1638.370018  
484      0.043318  -604.639954  
486      0.090457 -4387.509991  
487      0.031588  -696.459991  

[309 rows x 7 columns]

In [568]:
ratios.sort_values(by=['PE'], ascending=False).head(10)

ticker                            name       ROE      PB       PE  \
398    CRM              Salesforce.com Inc  0.003719    4.09  1098.69   
193      F              Ford Motor Company  0.001416    1.06   747.07   
302    MCK            McKesson Corporation  0.004201    3.02   717.88   
321    MYL                      Mylan N.V.  0.001414    0.81   572.80   
339   NLOK             NortonLifeLock Inc.  0.005400    7.85   459.80   
284    LYV  Live Nation Entertainment Inc.  0.060995   12.65   207.44   
57    ADSK                   Autodesk Inc. -1.542056 -296.67   192.38   
399   SBAC  SBA Communications Corporation -0.040085   -7.14   178.16   
7      AMD     Advanced Micro Devices Inc.  0.120623   19.01   157.60   
242   INCY              Incyte Corporation  0.056851    7.53   132.52   

            gain  
398  -138.890045  
193  -117.520001  
302 -7148.460083  
321  -356.600000  
339  -167.240004  
284  -220.189999  
57  -4565.930115  
399 -5716.230026  
7    -819.659998  
242 -1641.480011